In [76]:
import numpy as np
import matplotlib.pyplot as plt

# Original Galaxy Code

### The following sets up stars orbiting a center of mass

In [87]:
stars = 1000
X = []
Y = []
Z = []
vx = []
vy = []
vz = []
M = []
for i in range (0,stars):
    
    r = 1000*np.random.random()
    theta = np.pi*np.random.random()
    phi = 2*np.pi*np.random.random()
    x = r*np.cos(phi)
    y = r*np.sin(phi)

    z = 0.01*np.random.random()
    if (np.random.random()<0.5):
        z = -z
    #r = (x**2+y**2+z**2)**.5
    #phi = np.arcsin(abs(y/r))
    
    if (x<0) and (y>0):
        phi = np.pi-phi
    if (x<0) and (y<0):
        phi = phi+np.pi
    if (x>0) and (y<0):
        phi = -phi
    #x = r*np.cos(phi)
    #y = r*np.sin(phi)
    #z = 0.0001*np.random.random()
    M.append(1)
    X.append(x)
    Y.append(y)
    Z.append(z)
    #V = 5000
    r=1000   #r = V/(r**.5) #fast stars at center
    if(x>0) and (y>0):
        d = 0.04*np.random.random()
        e = 0.04*np.random.random()
        vex = -r*abs(np.sin(phi))+d
        vey = r*abs(np.cos(phi))+e
        vez = 0
        if (np.random.random()<.5):
            vex = -r*abs(np.sin(phi))-d
        if (np.random.random()<.5):
            vey = r*abs(np.cos(phi))-e
        vx.append(vex*.1)
        vy.append(vey*.1)
        vz.append(vez*.1)
    if(x<0) and (y>0):
        d = 0.04*np.random.random()
        e = 0.04*np.random.random()
        vex = -r*abs(np.sin(phi))+d
        vey = -r*abs(np.cos(phi))+e
        vez = 0
        if (np.random.random()<.5):
            vex = -r*abs(np.sin(phi))-d
        if (np.random.random()<.5):
            vey = -r*abs(np.cos(phi))-e
        vx.append(vex*.1)
        vy.append(vey*.1)
        vz.append(vez*.1)
    if(x<0) and (y<0):
        d = 0.04*np.random.random()
        e = 0.04*np.random.random()
        vex = r*abs(np.sin(phi))+d
        vey = -r*abs(np.cos(phi))+e
        vez = 0
        if (np.random.random()<.5):
            vex = r*abs(np.sin(phi))-d
        if (np.random.random()<.5):
            vey = -r*abs(np.cos(phi))-e
        vx.append(vex*.1)
        vy.append(vey*.1)
        vz.append(vez*.1)
    if(x>0) and (y<0):
        d = 0.04*np.random.random()
        e = 0.04*np.random.random()
        vex = r*abs(np.sin(phi))+d
        vey = r*abs(np.cos(phi))+e
        vez = 0
        if (np.random.random()<.5):
            vex = r*abs(np.sin(phi))-d
        if (np.random.random()<.5):
            vey = r*abs(np.cos(phi))-e
        vx.append(vex*.1)
        vy.append(vey*.1)
        vz.append(vez*.1)

### Gravity a la Newton

In [88]:
def wavex(u,v,w,M,X,Y,Z):
    G = 20
    l = 1
    axold=0
    for i in range (0,len(X)):
        dx = u-X[i]
        dy = v-Y[i]
        dz = w-Z[i]
        d = (dx**2)+(dy**2)+(dz**2)

        if  (d>100):
            a = -G*M[i]/d
            ax = (dx/d**.5)*a
        
        if (d<100):
            ax = 0
        axold = axold+ax
    return(axold)
def wavey(u,v,w,M,X,Y,Z):
    l = 1
    G = 20
    ayold = 0
    for i in range (0,len(X)):
        dx = u-X[i]
        dy = v-Y[i]
        dz = w-Z[i]
        d = (dx**2)+(dy**2)+(dz**2)
        
        if(d>25):
            a = -G*M[i]/d
            ay = (dy/d**.5)*a
        
        if (d<25):
            ay = 0
       
        ayold = ayold+ay
    return(ayold)
def wavez(u,v,w,M,X,Y,Z):
    l = 1
    G = 20
    azold = 0
    for i in range (0,len(X)):
        dx = u-X[i]
        dy = v-Y[i]
        dz = w-Z[i]
        d = (dx**2)+(dy**2)+(dz**2)
        
        if (d>25):
            a = -G*M[i]/d
            az = (dz/d**.5)*a   
        
        if (d<25):
            az = 0
        azold = 0
    return(azold)

# BMCM Costas Method
### BMCM = Baryonic Matter Center of Mass 

### This tells the computer to "divide" the galaxy ito an N by N grid. Then it sums the mass of all the stars in each box and treats the box as a point particle. Every other star will later interact with these approximate point particles, which reduces the amount of necessary computations by a huge factor (on the order of N*N/(stars*stars)) It initializes the array of grid masses

In [89]:
#This breaks up your galaxy of size L into NxN chunks. The more chunks, the more time it will take your computer to figure out. 
#Hopefully you won't need too many, since this is supposed to make your life a little easier.
#Adjust the offset C if the length scale doesn't start at the origin
#ex: If your galaxy is centered on the origin, C should be half the galaxy's length :)
L=2000
N = 10

C = 1000
xcm = []
ycm = []
zcm = []
    #zcm = np.zeros((0,N))
Mcm = []
for j in range (0,N):
    for i in range (0,N):
        ycm.append(L/(2*N)+(i%N)*L/N-C)
        xcm.append(L/(2*N)+(j%N)*L/N-C)
        zcm.append(0)
        m = []
        for k in range(0,len(X)):
            if (X[k]>i*L/N-C) and (X[k]<(i+1)*L/N-C) and (Y[k]>j*L/N-C) and (Y[k]<(j+1)*L/N-C):
                m.append(120)       
        Mcm.append(np.sum(m))
                

plt.plot(X,Y,'o')
plt.show()
print(len(Mcm), len(xcm), len(ycm))

100 100 100


## Dark Matter Halo

In [90]:
#gal
def glob_x(X,Y,Z):
    
    r_sq = (X**2)+(Y**2)+(Z**2)
    r = r_sq**0.5
    a=0
    if (r>0):
        p = 1/r 
        a = 100/r
    a_xy = a*(((X**2)+(Y**2))**0.5/r)
    a_x = a_xy*(X/((X**2)+(Y**2))**0.5)
    a_y = a_xy*(Y/((X**2)+(Y**2))**0.5)
    a_z = a*Z/r
    return a_x
#BLACK HOLE
def glob_y(X,Y,Z):
    
    r_sq = (X**2)+(Y**2)+(Z**2)
    r = r_sq**0.5
    a=0
    if (r>0):
        p = 1/r 
        a = 100/r
    a_xy = a*(((X**2)+(Y**2))**0.5/r)
    a_x = a_xy*(X/((X**2)+(Y**2))**0.5)
    a_y = a_xy*(Y/((X**2)+(Y**2))**0.5)
    a_z = a*Z/r
    return a_y
#GLOBULAR Density p/r
def glob_z(X,Y,Z):
    
    r_sq = (X**2)+(Y**2)+(Z**2)
    r = r_sq**0.5
    a=0
    if (r>0):
        p = 1/r 
        a=100/r#a = 0.1
    a_xy = a*(((X**2)+(Y**2))**0.5/r)
    a_x = a_xy*(X/((X**2)+(Y**2))**0.5)
    a_y = a_xy*(Y/((X**2)+(Y**2))**0.5)
    a_z = a*Z/r
        
    return a_z

## The following runs the model controlled by the above functions

In [91]:
#Galaxy Orbiting
#Galaxy Disk
%matplotlib osx
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()



fig = plt.figure(dpi=200,facecolor='k')
#velocities and initial positions:

with writer.saving(fig, "Costas_Method_Galaxy.mp4", dpi=200): 
    for k in range (0,50000): #time measured in k's
        t = 0.01
        fig.clear()
        ax=fig.gca(projection='3d')
        for i in range (0,stars):    
            X[i] = X[i]+t*vx[i]
        
            Y[i] = Y[i]+t*vy[i]
        
            Z[i] = Z[i]+t*vz[i]
        for i in range (0,stars): 
            #if (vx[i]<V) and (vy[i]<V) and (vz[i]<V):
            vx[i] = vx[i]-glob_x(X[i],Y[i],Z[i])+wavex(X[i],Y[i],Z[i],Mcm,xcm,ycm,zcm)
            vy[i] = vy[i]-glob_y(X[i],Y[i],Z[i])+wavey(X[i],Y[i],Z[i],Mcm,xcm,ycm,zcm)
            vz[i] = vz[i]-glob_z(X[i],Y[i],Z[i])+wavez(X[i],Y[i],Z[i],Mcm,xcm,ycm,zcm)
            
                

            #print(vz,Z)
        
        if (k%10==0):
            ax.set_xlim(-1000, 1000) 
            ax.set_ylim(-1000, 1000)   
            ax.set_zlim(-1000, 1000)
            ax.scatter(X[0:stars//4],Y[0:stars//4],Z[0:stars//4],marker='o',s=.01, color = 'white', antialiased=False)
            ax.scatter(X[stars//4:3*stars//4],Y[stars//4:3*stars//4],Z[stars//4:3*stars//4],marker='o',s=.01, color = 'white', antialiased=False)
            ax.scatter(X[3*stars//4:9*stars//10],Y[3*stars//4:9*stars//10],Z[3*stars//4:9*stars//10], marker='o',s=.1, color = 'white', antialiased=False)
            ax.scatter(X[9*stars//10:],Y[9*stars//10:],Z[9*stars//10:], marker='o',s=.01, color = 'white', antialiased=False)
     
            ax.set_facecolor('black')
            ax.grid(False)
    
            fig.set_facecolor('black')
            ax.set_facecolor('black')
            ax.grid(False)
        #ax.view_init(elev=0, azim=50)
            ax.w_xaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_yaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_zaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_xaxis.pane.fill = False
            ax.w_yaxis.pane.fill = False
            ax.w_zaxis.pane.fill = False
        #ax.w_xaxis.set_pane_color('k',0,0)
        #ax.w_yaxis.set_pane_color()
        #ax.w_zaxis.set_pane_color()
            ax.set_title("Spiral Galaxy", color = 'white')
        #ax.view_init(30, 45,45)
            plt.draw()
            plt.pause(0.05)
            writer.grab_frame()
            #The Costas Method has to run in this loop, otherwise you get a spooky gravity from the past. boo!
            xcm = []
            ycm = []
            zcm = []
            #zcm = np.zeros((0,N))
            Mcm = []
            for j in range (0,N):
                for i in range (0,N):
                    #xcm.append(L/(2*N)+(i%N)*L/N)
                    #ycm.append(L/(2*N)+(j%N)*L/N)
                    #zcm.append(0)
                    m=[]
                    for k in range(0,len(X)):
                        if (X[k]>i*L/N-C) and (X[k]<(i+1)*L/N-C) and (Y[k]>j*L/N-C) and (Y[k]<(j+1)*L/N-C):
                            m.append(120)       
                    Mcm.append(np.sum(m))


KeyboardInterrupt



# Globular Cluster

In [73]:
stars = 1000 #we can have a lot more stars here because there are far fewer calulations that need to be done
X = []
Y = []
Z = []
vx = []
vy = []
vz = []
M = []
for i in range (0,stars//2):
    
    r = 1000*np.random.random()
    theta = np.pi*np.random.random()
    phi = np.pi*np.random.random()+np.pi/2
    x = r*np.cos(phi)*np.sin(theta)
    y = r*np.sin(phi)*np.sin(theta)
    z = r*np.cos(theta)
    
    v_x = 40*np.random.random() 
    v_y = 40*np.random.random()
    v_z = 40*np.random.random()
    if (np.random.random()<0.5):
        v_x *= -1
    if(np.random.random()<0.5):
        v_y *=-1
    if(np.random.random()<0.5):
        v_z *=-1
    X.append(x)
    Y.append(y)
    Z.append(z)
    vx.append(v_x)
    vy.append(v_y)
    vz.append(v_z)
    
for i in range (stars//2,stars): #This does the stars within phi=-pi/2 and phi = pi/2
    
    r = 1000*np.random.random()
    theta = np.pi*np.random.random()
    phi = np.pi*np.random.random()-np.pi/2
    x = r*np.cos(phi)*np.sin(theta)
    y = r*np.sin(phi)*np.sin(theta)
    z = r*np.cos(theta)
    
    v_x = 40*np.random.random() 
    v_y = 40*np.random.random()
    v_z = 40*np.random.random()
    if (np.random.random()<0.5):
        v_x *= -1
    if(np.random.random()<0.5):
        v_y *=-1
    if(np.random.random()<0.5):
        v_z *=-1
    X.append(x)
    Y.append(y)
    Z.append(z)
    vx.append(v_x)
    vy.append(v_y)
    vz.append(v_z)

In [75]:
#Galaxy Orbiting
#Galaxy Disk
%matplotlib osx
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure()



fig = plt.figure(dpi=200,facecolor='k')
#velocities and initial positions:

with writer.saving(fig, "Costas_Globular_Cluster.mp4", dpi=200): 
    for k in range (0,50000): #time measured in k's
        t = 0.01
        fig.clear()
        ax=fig.gca(projection='3d')
        for i in range (0,stars):    
            X[i] = X[i]+t*vx[i]
        
            Y[i] = Y[i]+t*vy[i]
        
            Z[i] = Z[i]+t*vz[i]
        for i in range (0,stars): 
            #if (vx[i]<V) and (vy[i]<V) and (vz[i]<V):
            vx[i] = vx[i]-glob_x(X[i],Y[i],Z[i])
            vy[i] = vy[i]-glob_y(X[i],Y[i],Z[i])
            vz[i] = vz[i]-glob_z(X[i],Y[i],Z[i])
                
            
            #this loop creates a list of stars that start off 
            
        if (k%10==0):
            ax.set_xlim(-1000, 1000) 
            ax.set_ylim(-1000, 1000)   
            ax.set_zlim(-1000, 1000)
            ax.scatter(X[0:stars//2],Y[0:stars//2],Z[0:stars//2],marker='o',s=.01, color = 'yellow', antialiased=False)
            ax.scatter(X[stars//2:stars],Y[stars//2:stars],Z[stars//2:stars],marker='o',s=.01, color = 'red', antialiased=False)
            
     
            ax.set_facecolor('black')
            ax.grid(False)
    
            fig.set_facecolor('black')
            ax.set_facecolor('black')
            ax.grid(False)
        #ax.view_init(elev=0, azim=50)
            ax.w_xaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_yaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_zaxis.set_pane_color((0.0, 0.0, 0.0, 0.0))
            ax.w_xaxis.pane.fill = False
            ax.w_yaxis.pane.fill = False
            ax.w_zaxis.pane.fill = False
        #ax.w_xaxis.set_pane_color('k',0,0)
        #ax.w_yaxis.set_pane_color()
        #ax.w_zaxis.set_pane_color()
            ax.set_title("Globular Cluster", color = 'white')
        #ax.view_init(30, 45,45)
            plt.draw()
            plt.pause(0.05)
            writer.grab_frame()
            #The Costas Method is not needed in this loop, since we only want to look at the effects of Dark Matter :)
            

KeyboardInterrupt: 